## BERT PIPELINE

In [1]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
!pip install simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import f1_score, recall_score, precision_score
from sklearn.metrics import matthews_corrcoef

# Check GPU
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 4.7 MB/s 
     |████████████████████████████████| 441 kB 64.6 MB/s 
     |████████████████████████████████| 7.6 MB 86.4 MB/s 
     |████████████████████████████████| 1.3 MB 67.5 MB/s 
     |████████████████████████████████| 43 kB 2.4 MB/s 
     |████████████████████████████████| 9.2 MB 54.9 MB/s 
     |████████████████████████████████| 5.5 MB 77.1 MB/s 
     |████████████████████████████████| 1.9 MB 76.1 MB/s 
     |████████████████████████████████| 163 kB 87.4 MB/s 
     |████████████████████████████████| 166 kB 86.6 MB/s 
     |████████████████████████████████| 182 kB 79.4 MB/s 
     |████████████████████████████████| 63 kB 2.1 MB/s 
     |████████████████████████████████| 166 kB 84.5 MB/s 
     |████████████████████████████████| 162 kB 93.1 MB/s 
     |████████████████████████████████| 162 kB 95.8 MB/s 
     |██████████████████████████████

In [2]:
# Load the dataset from google drive
from google.colab import drive
drive.mount('/content/drive')

# Import downsampled dataset
df = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_downsampled.xlsx')

# Import without google drive
# df = pd.read_excel('DATASET_downsampled.xlsx')

df = df.drop(columns = ['Unnamed: 0'])

df.info()

Mounted at /content/drive
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       2592 non-null   object
 1   kano_labels  2592 non-null   object
 2   labels       2592 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 60.9+ KB


In [3]:
# Show the distribution of the labels
print(df['labels'].value_counts())

0    648
2    648
3    648
1    648
Name: labels, dtype: int64


In [4]:
# Rename the columns so that simple transformers can handle them
train_data = df[['review','labels']]
train_data.columns = ['text', 'labels']
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    2592 non-null   object
 1   labels  2592 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 40.6+ KB


In [5]:
# Model implementation and k-fold cross validation with Simpletransformers

# Wrapper function to calculate f1-score with additional parameters
def f1_multiclass(labels, preds):
    return f1_score(labels, preds, average = None)

# Wrapper function to calculate recall with additional parameters
def recall_multiclass(labels, preds):
    return recall_score(labels, preds, average = None)

# Wrapper function to calculate precision with additional parameters
def precision_multiclass(labels, preds):
    return precision_score(labels, preds, average = None)

# K-fold cross validation with 10 folds
n = 10
kf = KFold(n_splits=n, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc = []
resultsf1 = []
resultsPrecision = []
resultsRecall = []

model_args = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create the ClassificationModel
model = ClassificationModel(
    'bert',
    'bert-base-cased',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf.split(train_data):
  train_df = train_data.iloc[train_index]
  val_df = train_data.iloc[val_index]

  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(val_df, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)
  print(result)
  
  # Add scores to the respective lists
  resultsAcc.append(result['acc'])
  resultsf1.append(result['f1'])
  resultsPrecision.append(result['precision'])
  resultsRecall.append(result['recall'])

  print("results accuracy",resultsAcc)
  print(f"Mean-Precision: {sum(resultsAcc) / len(resultsAcc)}")
  print('results f1: ', resultsf1)
  print('results precision: ', resultsPrecision)
  print('results recall: ', resultsRecall)

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/436M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at b

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/213k [00:00<?, ?B/s]

...

{'mcc': 0.9896742497330304, 'f1': array([0.9929078 , 1.        , 0.99300699, 0.98461538]), 'acc': 0.9922779922779923, 'recall': array([1.        , 1.        , 0.98611111, 0.98461538]), 'precision': array([0.98591549, 1.        , 1.        , 0.98461538]), 'eval_loss': 0.05964005053652782}
results accuracy [0.7269230769230769, 0.8346153846153846, 0.8764478764478765, 0.8803088803088803, 0.9536679536679536, 0.9806949806949807, 0.9768339768339769, 0.9922779922779923, 0.9922779922779923]
Mean-Precision: 0.9126720126720128
results f1:  [array([0.88405797, 0.67164179, 0.78125   , 0.55      ]), array([0.91935484, 0.79452055, 0.90510949, 0.7079646 ]), array([0.944     , 0.83969466, 0.928     , 0.80291971]), array([0.95726496, 0.82857143, 0.94488189, 0.80597015]), array([0.97744361, 0.95172414, 0.97247706, 0.91603053]), array([0.98387097, 0.97101449, 0.98507463, 0.98360656]), array([0.99310345, 0.96296296, 0.99130435, 0.95934959]), array([1.        , 0.98275862, 0.98630137, 1.        ]), array([0

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 1.0, 'f1': array([1., 1., 1., 1.]), 'acc': 1.0, 'recall': array([1., 1., 1., 1.]), 'precision': array([1., 1., 1., 1.]), 'eval_loss': 0.0003403327383707757}
results accuracy [0.7269230769230769, 0.8346153846153846, 0.8764478764478765, 0.8803088803088803, 0.9536679536679536, 0.9806949806949807, 0.9768339768339769, 0.9922779922779923, 0.9922779922779923, 1.0]
Mean-Precision: 0.9214048114048115
results f1:  [array([0.88405797, 0.67164179, 0.78125   , 0.55      ]), array([0.91935484, 0.79452055, 0.90510949, 0.7079646 ]), array([0.944     , 0.83969466, 0.928     , 0.80291971]), array([0.95726496, 0.82857143, 0.94488189, 0.80597015]), array([0.97744361, 0.95172414, 0.97247706, 0.91603053]), array([0.98387097, 0.97101449, 0.98507463, 0.98360656]), array([0.99310345, 0.96296296, 0.99130435, 0.95934959]), array([1.        , 0.98275862, 0.98630137, 1.        ]), array([0.9929078 , 1.        , 0.99300699, 0.98461538]), array([1., 1., 1., 1.])]
results precision:  [array([0.85915493, 0.671

In [6]:
print("results accuracy",resultsAcc)
print('results f1: ', resultsf1)
print('results precision: ', resultsPrecision)
print('results recall: ', resultsRecall)

results accuracy [0.7269230769230769, 0.8346153846153846, 0.8764478764478765, 0.8803088803088803, 0.9536679536679536, 0.9806949806949807, 0.9768339768339769, 0.9922779922779923, 0.9922779922779923, 1.0]
results f1:  [array([0.88405797, 0.67164179, 0.78125   , 0.55      ]), array([0.91935484, 0.79452055, 0.90510949, 0.7079646 ]), array([0.944     , 0.83969466, 0.928     , 0.80291971]), array([0.95726496, 0.82857143, 0.94488189, 0.80597015]), array([0.97744361, 0.95172414, 0.97247706, 0.91603053]), array([0.98387097, 0.97101449, 0.98507463, 0.98360656]), array([0.99310345, 0.96296296, 0.99130435, 0.95934959]), array([1.        , 0.98275862, 0.98630137, 1.        ]), array([0.9929078 , 1.        , 0.99300699, 0.98461538]), array([1., 1., 1., 1.])]
results precision:  [array([0.85915493, 0.67164179, 0.75757576, 0.58928571]), array([0.91935484, 0.71604938, 0.95384615, 0.76923077]), array([0.90769231, 0.83333333, 0.95081967, 0.82089552]), array([0.98245614, 0.77333333, 0.96774194, 0.83076923

In [7]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

def PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1):

  np_resultsPrecision = np.array(resultsPrecision)
  np_resultsRecall = np.array(resultsRecall)
  np_resultsf1  = np.array(resultsf1)

  # Calculate the mean precision for each label
  df_resultsPrecision = pd.DataFrame(np_resultsPrecision, columns=list('BDIP'))
  precision_b_mean = df_resultsPrecision['B'].mean()
  precision_d_mean = df_resultsPrecision['D'].mean()
  precision_i_mean = df_resultsPrecision['I'].mean()
  precision_p_mean = df_resultsPrecision['P'].mean()

  # Calculate the mean recall for each label
  df_resultsRecall = pd.DataFrame(np_resultsRecall, columns=list('BDIP'))
  recall_b_mean = df_resultsRecall['B'].mean()
  recall_d_mean = df_resultsRecall['D'].mean()
  recall_i_mean = df_resultsRecall['I'].mean()
  recall_p_mean = df_resultsRecall['P'].mean()

  # Calculate the mean f1-score for each label
  df_resultsf1 = pd.DataFrame(np_resultsf1, columns=list('BDIP'))
  f1_b_mean = df_resultsf1['B'].mean()
  f1_d_mean = df_resultsf1['D'].mean()
  f1_i_mean = df_resultsf1['I'].mean()
  f1_p_mean = df_resultsf1['P'].mean()

  # Create dataframe with summarized results
  metrics = [{'B': precision_b_mean, 'D': precision_d_mean, 'I': precision_i_mean, 'P':precision_p_mean},
          {'B': recall_b_mean, 'D': recall_d_mean, 'I': recall_i_mean, 'P': recall_p_mean},
          {'B': f1_b_mean, 'D': f1_d_mean, 'I': f1_i_mean, 'P': f1_p_mean} ]
  train_df_metrics = pd.DataFrame(metrics, index=['Average precision',
                                'Average recall',
                                'Average F1-Score'])
  return train_df_metrics

PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1)

B         D         I         P
Average precision  0.959490  0.886111  0.961506  0.882324
Average recall     0.971519  0.917377  0.937024  0.861459
Average F1-Score   0.965200  0.900289  0.948741  0.871046

## Training on the dataset at hand, testing on the 'Trainingskorpus' dataset

In [8]:
# Import of 'Trainingskorpus_Final', which gives the final labeling
testset1 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_Final.xlsx')

# Import without google drive
# testset1 = pd.read_excel('Trainingskorpus_Final.xlsx')

testset1 = testset1.drop(columns = ['Unnamed: 0'])
testset1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
dtypes: object(2)
memory usage: 25.5+ KB


In [9]:
# Show the distribution of the labels
print(testset1['kano_labels'].value_counts())

B    1102
P     395
D      95
I      30
Name: kano_labels, dtype: int64


In [10]:
# Import of 'Trainingskorpus_InitialLabels', which gives the initial labeling of two sometimes differing labels
testset2 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_InitialLabels.xlsx')

# Import without google drive
# testset2 = pd.read_excel('Trainingskorpus_InitialLabels.xlsx')

testset2 = testset2.drop(columns = ['Unnamed: 0'])
testset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   review   1622 non-null   object
 1   label 1  1622 non-null   object
 2   label 2  1622 non-null   object
dtypes: object(3)
memory usage: 38.1+ KB


In [11]:
# Merge the two sets so we have the final labels as well as the initial labels in the testset
testset = testset1.merge(testset2, left_on='review', right_on='review')
testset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1622 entries, 0 to 1621
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
 2   label 1      1622 non-null   object
 3   label 2      1622 non-null   object
dtypes: object(4)
memory usage: 63.4+ KB


In [12]:
# Add a column 'equal' which is True if the two initial labels are equal and false otherwise

equal = [None]*np.size(testset['review'])

i = 0
for label1, label2 in zip(testset2['label 1'], testset2['label 2']):
  if(label1 == label2):
    equal[i] = True
  else:
    equal[i] = False
  i += 1
  
testset['equal'] = equal

In [13]:
# Calculate the accuracy of the whole testset as well as 
# only the parts where the inital two labels are equal (accuracy_clear)
# or differ (accuracy_diff)

accuracy_clear = 0.
accuracy_diff = 0.
n_clear = 0
n_diff = 0
all_predicted_labels = []
predicted_labels_equal_initial_label = []
predicted_labels_diff_initial_label = []
true_label_equal = []
true_label_diff = []

for label, review, equal in zip(testset['kano_labels'],  testset['review'], testset['equal']):
  
  test_prediction, raw_outputs = model.predict([review])
  
  predicted_label = ''

  if test_prediction[0] == 0:
    predicted_label = 'B'
  if test_prediction[0] == 1:
    predicted_label = 'D'
  if test_prediction[0] == 2:
    predicted_label = 'I'
  if test_prediction[0] == 3:
    predicted_label = 'P'

  all_predicted_labels.append(predicted_label)
  
  if equal:
    n_clear += 1
    predicted_labels_equal_initial_label.append(predicted_label)
    true_label_equal.append(label)
    if label == predicted_label:
      accuracy_clear += 1.

  if not equal:
    n_diff += 1
    predicted_labels_diff_initial_label.append(predicted_label)
    true_label_diff.append(label)
    if label == predicted_label:
      accuracy_diff += 1.

accuracy = (accuracy_clear + accuracy_diff) / (n_clear + n_diff)

accuracy_clear /= n_clear
accuracy_diff /= n_diff

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
print('Accuracy Trainingskorpus:                                                  ', round(accuracy*100, 2), '%,  n =', (n_clear + n_diff))
print('Accuracy Trainingskorpus only on the data that coincides on initial labels:', round(accuracy_clear*100, 2), '%,  n =', n_clear)
print('Accuracy Trainingskorpus only on the data that differs on initial labels:  ', round(accuracy_diff*100, 2), '%,  n = ', n_diff)

Accuracy Trainingskorpus:                                                   68.0 %,  n = 1622
Accuracy Trainingskorpus only on the data that coincides on initial labels: 67.82 %,  n = 1383
Accuracy Trainingskorpus only on the data that differs on initial labels:   69.04 %,  n =  239


In [15]:
# Calculate precision, recall and f1-score for each label

test_df_metrics = precision_recall_fscore_support(testset['kano_labels'], all_predicted_labels, average=None,labels=['B', 'D', 'I', 'P'])

print('Precision B: ', test_df_metrics[0][0])
print('Precision D: ', test_df_metrics[0][1])
print('Precision I: ', test_df_metrics[0][2])
print('Precision P: ', test_df_metrics[0][3])

print('Recall B: ', test_df_metrics[1][0])
print('Recall D: ', test_df_metrics[1][1])
print('Recall I: ', test_df_metrics[1][2])
print('Recall P: ', test_df_metrics[1][3])

print('F1-score B: ', test_df_metrics[2][0])
print('F1-score D: ', test_df_metrics[2][1])
print('F1-score I: ', test_df_metrics[2][2])
print('F1-score P: ', test_df_metrics[2][3])

Precision B:  0.8965909090909091
Precision D:  0.40119760479041916
Precision I:  0.5
Precision P:  0.4293193717277487
Recall B:  0.7159709618874773
Recall D:  0.7052631578947368
Recall I:  0.03333333333333333
Recall P:  0.6227848101265823
F1-score B:  0.7961654894046417
F1-score D:  0.5114503816793894
F1-score I:  0.0625
F1-score P:  0.5082644628099173


In [16]:
# Calculates the phi-coefficient for labels where both researchers agreed vs. where they disagreed

print('MCC for labels where both researchers agreed: ',matthews_corrcoef(true_label_equal, predicted_labels_equal_initial_label))
print('MCC for labels where both researchers disagreed: ',matthews_corrcoef(true_label_diff, predicted_labels_diff_initial_label))

MCC for labels where both researchers agreed:  0.4194541587796626
MCC for labels where both researchers disagreed:  0.4350103984505499


## Combine dataset at hand and 'Trainingskorpus' dataset, then do Train-Test-Split

In [17]:
# Import combined downsampled dataset 
df_combined = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_Trainingskorpus_combined.xlsx')
df_combined = df_combined.drop(columns = ['Unnamed: 0'])

# Import without google drive
# df_combined = pd.read_excel('DATASET_Trainingskorpus_combined.xlsx')

# Rename column so that simple transformers can handle it
df_combined = df_combined.rename(columns = {'review': 'text'})
df_combined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2972 entries, 0 to 2971
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   text         2972 non-null   object
 1   kano_labels  2972 non-null   object
 2   labels       2972 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 69.8+ KB


In [18]:
# Show the distribution of the labels
print(df_combined['labels'].value_counts())

2    743
3    743
1    743
0    743
Name: labels, dtype: int64


In [19]:
# 10-fold cross validation on the combined dataset

n2 = 10
kf2 = KFold(n_splits=n2, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc2 = []
resultsf12 = []
resultsPrecision2 = []
resultsRecall2 = []

model_args2 = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create a ClassificationModel
model2 = ClassificationModel(
    'bert',
    'bert-base-cased',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf2.split(df_combined):
  train_df2 = df_combined.iloc[train_index]
  val_df2 = df_combined.iloc[val_index]

  model2.train_model(df_combined)
  result2, model_outputs2, wrong_predictions2 = model2.eval_model(val_df2, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)

  print(result2)
  # Add scores to the respective lists
  resultsAcc2.append(result2['acc'])
  resultsf12.append(result2['f1'])
  resultsPrecision2.append(result2['precision'])
  resultsRecall2.append(result2['recall'])

  print("results accuracy",resultsAcc2)
  print(f"Mean-Precision: {sum(resultsAcc2) / len(resultsAcc2)}")
  print('results f1: ', resultsf12)
  print('results precision: ', resultsPrecision2)
  print('results recall: ', resultsRecall2)


Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at b

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

...

{'mcc': 0.991006295103287, 'f1': array([0.98387097, 0.99363057, 1.        , 0.99386503]), 'acc': 0.9932659932659933, 'recall': array([0.98387097, 1.        , 1.        , 0.98780488]), 'precision': array([0.98387097, 0.98734177, 1.        , 1.        ]), 'eval_loss': 0.11804051344331942}
results accuracy [0.8355704697986577, 0.9060402684563759, 0.9326599326599326, 0.9562289562289562, 0.9865319865319865, 0.9831649831649831, 0.9932659932659933, 0.9932659932659933, 0.9932659932659933]
Mean-Precision: 0.9533327307376523
results f1:  [array([0.93478261, 0.78481013, 0.92537313, 0.65      ]), array([0.90780142, 0.91860465, 0.98064516, 0.796875  ]), array([0.96774194, 0.91139241, 0.97297297, 0.87218045]), array([0.95757576, 0.95726496, 0.98224852, 0.92307692]), array([0.984375  , 0.98136646, 1.        , 0.98159509]), array([0.98701299, 0.97260274, 0.98701299, 0.98571429]), array([0.99328859, 0.9875    , 0.99236641, 1.        ]), array([0.99300699, 0.98684211, 1.        , 0.9929078 ]), array([0.

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 1.0, 'f1': array([1., 1., 1., 1.]), 'acc': 1.0, 'recall': array([1., 1., 1., 1.]), 'precision': array([1., 1., 1., 1.]), 'eval_loss': 0.0030188631070287605}
results accuracy [0.8355704697986577, 0.9060402684563759, 0.9326599326599326, 0.9562289562289562, 0.9865319865319865, 0.9831649831649831, 0.9932659932659933, 0.9932659932659933, 0.9932659932659933, 1.0]
Mean-Precision: 0.957999457663887
results f1:  [array([0.93478261, 0.78481013, 0.92537313, 0.65      ]), array([0.90780142, 0.91860465, 0.98064516, 0.796875  ]), array([0.96774194, 0.91139241, 0.97297297, 0.87218045]), array([0.95757576, 0.95726496, 0.98224852, 0.92307692]), array([0.984375  , 0.98136646, 1.        , 0.98159509]), array([0.98701299, 0.97260274, 0.98701299, 0.98571429]), array([0.99328859, 0.9875    , 0.99236641, 1.        ]), array([0.99300699, 0.98684211, 1.        , 0.9929078 ]), array([0.98387097, 0.99363057, 1.        , 0.99386503]), array([1., 1., 1., 1.])]
results precision:  [array([0.88659794, 0.7126

In [20]:
print("results accuracy",resultsAcc2)
print('results f1: ', resultsf12)
print('results precision: ', resultsPrecision2)
print('results recall: ', resultsRecall2)

results accuracy [0.8355704697986577, 0.9060402684563759, 0.9326599326599326, 0.9562289562289562, 0.9865319865319865, 0.9831649831649831, 0.9932659932659933, 0.9932659932659933, 0.9932659932659933, 1.0]
results f1:  [array([0.93478261, 0.78481013, 0.92537313, 0.65      ]), array([0.90780142, 0.91860465, 0.98064516, 0.796875  ]), array([0.96774194, 0.91139241, 0.97297297, 0.87218045]), array([0.95757576, 0.95726496, 0.98224852, 0.92307692]), array([0.984375  , 0.98136646, 1.        , 0.98159509]), array([0.98701299, 0.97260274, 0.98701299, 0.98571429]), array([0.99328859, 0.9875    , 0.99236641, 1.        ]), array([0.99300699, 0.98684211, 1.        , 0.9929078 ]), array([0.98387097, 0.99363057, 1.        , 0.99386503]), array([1., 1., 1., 1.])]
results precision:  [array([0.88659794, 0.71264368, 0.95384615, 0.79591837]), array([0.87671233, 0.88764045, 1.        , 0.85      ]), array([0.94936709, 0.9       , 0.97297297, 0.90625   ]), array([0.91860465, 0.96551724, 0.98809524, 0.95652174

In [21]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

PrecisionRecallF1Table(resultsPrecision2, resultsRecall2, resultsf12)

B         D         I         P
Average precision  0.958654  0.931256  0.991491  0.950869
Average recall     0.984456  0.969728  0.976923  0.894117
Average F1-Score   0.970946  0.949401  0.984062  0.919621